In [1]:
!pip install transformers accelerate bitsandbytes sentencepiece einops

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 15.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 251.2/251.2 kB 24.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 92.6/92.6 MB 10.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 57.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 4.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 26.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 75.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 71.2 MB/s eta 0:00:00


In [2]:
import torch
from transformers import AutoModelForCausalLM, AutoTokenizer

TOKENIZER_ID = "AIBunCho/japanese-novel-gpt-j-6b"
MODEL_ID = "tsukemono/japanese-novel-gpt-j-6b-f16-marisa"

In [3]:
# tokenizer設定
tokenizer = AutoTokenizer.from_pretrained(TOKENIZER_ID, use_fast=True)
ret_token = tokenizer("[SEP]",  truncation=True, add_special_tokens=False)['input_ids'][-1]
bra_token = tokenizer("（",  truncation=True, add_special_tokens=False)['input_ids'][-1]

/usr/local/lib/python3.10/dist-packages/transformers/convert_slow_tokenizer.py:470: UserWarning: The sentencepiece tokenizer that you are converting to a fast tokenizer uses the byte fallback option which is not implemented in the fast tokenizers. In practice this means that the fast version of the tokenizer can produce unknown tokens whereas the sentencepiece version would have converted these unknown tokens into a sequence of byte tokens matching the original piece of text.
  warnings.warn(
Asking to truncate to max_length but no maximum length is provided and the model has no predefined maximum length. Default to no truncation.


In [6]:
# model設定
model = AutoModelForCausalLM.from_pretrained(MODEL_ID, device_map="auto", load_in_8bit=False, torch_dtype=torch.float16)
model.eval()

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

GPTJForCausalLM(
  (transformer): GPTJModel(
    (wte): Embedding(50400, 4096)
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-27): 28 x GPTJBlock(
        (ln_1): LayerNorm((4096,), eps=1e-05, elementwise_affine=True)
        (attn): GPTJAttention(
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
          (k_proj): Linear(in_features=4096, out_features=4096, bias=False)
          (v_proj): Linear(in_features=4096, out_features=4096, bias=False)
          (q_proj): Linear(in_features=4096, out_features=4096, bias=False)
          (out_proj): Linear(in_features=4096, out_features=4096, bias=False)
        )
        (mlp): GPTJMLP(
          (fc_in): Linear(in_features=4096, out_features=16384, bias=True)
          (fc_out): Linear(in_features=16384, out_features=4096, bias=True)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
    )
    (ln_f)

In [7]:
# テキスト生成関数の定義
def generate(text,input=None,maxTokens=512):
    prompt = f"ユーザー: {text}[SEP]魔理沙: "
    input_ids = tokenizer(prompt,
        return_tensors="pt",
        truncation=True,
        add_special_tokens=False
    ).input_ids.cuda()
    with torch.no_grad():
        outputs = model.generate(
            input_ids = input_ids,
            max_length=maxTokens,
            # max_new_tokens=50,
            do_sample=True,
            temperature=0.1,
            top_p=0.9,
            top_k=20,
            no_repeat_ngram_size=2,
            repetition_penalty=1.15,
            pad_token_id=tokenizer.pad_token_id,
            bad_words_ids=[[bra_token]],
            eos_token_id = [tokenizer.eos_token_id,ret_token]
        )
    outputs = tokenizer.decode(outputs.tolist()[0][input_ids.size(1):],skip_special_tokens=True)
    return outputs

In [8]:
generate("幻想郷ってどんな場所?")

'そうだな。一言で言えば、幻想の世界だ! '

In [16]:
generate("仏教についてどう思う?")

'そうだな。私は、宗教はよく分からないが......ただ、神様ってのは本当にいると思うぜ。 '

In [10]:
generate("日本で一番高い山は?")

'富士山だ!'

In [17]:
generate("自己紹介してください")

'霧雨魔理沙だ。普通の魔法使いだぜ! '